In [5]:
from google.colab import drive
drive.mount("/content/drive")



Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
from google.colab import files
files.upload()  # Upload kaggle.json


Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"jayapriyasundar","key":"dc93530ad11512013b17d21ebb382ab8"}'}

In [ ]:
!mkdir -p ~/.kaggle
!mv kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json


In [ ]:
!kaggle datasets download -d tuyenldvn/caucafall -p /content/ --force


Dataset URL: https://www.kaggle.com/datasets/tuyenldvn/caucafall
License(s): unknown
100% 7.74G/7.76G [01:32<00:00, 95.4MB/s]
100% 7.76G/7.76G [01:33<00:00, 89.5MB/s]


In [ ]:
import zipfile
import os
import shutil

dataset_path = "/content/caucafall.zip"  # ZIP file
extract_path = "/content/Dataset_CAUCALFall"  # Temporary extraction folder
target_subjects = ["Subject.1", "Subject.2"]  # Modify as needed

# Unzip only the required subject folders
with zipfile.ZipFile(dataset_path, "r") as zip_ref:
    for file in zip_ref.namelist():
        if any(f"CAUCAFall/{sub}/" in file for sub in target_subjects):  # Check for subject paths
            zip_ref.extract(file, extract_path)

# Move extracted subject folders to Google Drive
drive_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"
os.makedirs(drive_path, exist_ok=True)  # Ensure the directory exists

for subject in target_subjects:
    src = os.path.join(extract_path, "Dataset CAUCAFall", "CAUCAFall", subject)
    dest = os.path.join(drive_path, subject)
    if os.path.exists(src):
        shutil.move(src, dest)
        print(f"Moved {subject} to Google Drive.")
    else:
        print(f"Warning: {subject} not found in extracted files!")

print("✅ Extraction and transfer complete!")


Moved Subject.1 to Google Drive.
Moved Subject.2 to Google Drive.
✅ Extraction and transfer complete!


In [ ]:
!ls "/content/drive/My Drive/fall_detection_data/CAUCAFall"


Subject.1  Subject.2


In [ ]:
!ls "/content/drive/My Drive/fall_detection_data/CAUCAFall/Subject.1"


'Fall backwards'  'Fall left'	'Fall sitting'	 Kneel		  'Sit down'
'Fall forward'	  'Fall right'	 Hop		'Pick up object'   Walk


In [ ]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images (320x320 as an example)
target_size = (320, 320)

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        # Assuming the annotation format is: class_id x1 y1 x2 y2
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        # Calculate the resize ratios
        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        # Adjust bounding box coordinates
        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        # Save the new annotation (format: class_id x1 y1 x2 y2)
        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Save the resized image
    resized_image_path = image_path.replace(dataset_path, dataset_path + "/resized_images")
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    image_resized.save(resized_image_path)

    # Save the updated annotations
    resized_annotation_path = annotation_path.replace(dataset_path, dataset_path + "/resized_annotations")
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f"Resized image saved to: {resized_image_path}")
    print(f"Updated annotations saved to: {resized_annotation_path}")

# Example usage for the first subject
subject_folder = os.path.join(dataset_path, "Subject.1")

# Iterate through activities and process images and annotations
for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")  # Assuming annotations have same name as image
                resize_image_and_annotations(image_path, annotation_path, target_size)


Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.1/Pick up object/res100096.png
Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.1/Pick up object/res100096.txt
Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.1/Pick up object/res100067.png
Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.1/Pick up object/res100067.txt
Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.1/Pick up object/res100085.png
Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.1/Pick up object/res100085.txt
Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.1/Pick up object/res100031.png
Updated annotations saved to: /content/driv

In [ ]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images (320x320 as an example)
target_size = (320, 320)

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        # Assuming the annotation format is: class_id x1 y1 x2 y2
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        # Calculate the resize ratios
        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        # Adjust bounding box coordinates
        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        # Save the new annotation (format: class_id x1 y1 x2 y2)
        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Save the resized image
    resized_image_path = image_path.replace(dataset_path, dataset_path + "/resized_images")
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    image_resized.save(resized_image_path)

    # Save the updated annotations
    resized_annotation_path = annotation_path.replace(dataset_path, dataset_path + "/resized_annotations")
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f"Resized image saved to: {resized_image_path}")
    print(f"Updated annotations saved to: {resized_annotation_path}")

# Example usage for the first subject
subject_folder = os.path.join(dataset_path, "Subject.2")

# Iterate through activities and process images and annotations
for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")  # Assuming annotations have same name as image
                resize_image_and_annotations(image_path, annotation_path, target_size)


Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.2/Pick up object/res200033.png
Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.2/Pick up object/res200033.txt
Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.2/Pick up object/res200164.png
Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.2/Pick up object/res200164.txt
Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.2/Pick up object/res200138.png
Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.2/Pick up object/res200138.txt
Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.2/Pick up object/res200024.png
Updated annotations saved to: /content/driv

In [1]:
from google.colab import drive
drive.mount("/content/drive")

Mounted at /content/drive


In [2]:
from google.colab import files
files.upload()  # Upload kaggle.json

Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"jayapriyasundar","key":"ce22c877a3703a19c9e0d05de263a78d"}'}

In [3]:
!mkdir -p ~/.kaggle
!mv kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

In [4]:
!kaggle datasets download -d tuyenldvn/caucafall -p /content/ --force


Dataset URL: https://www.kaggle.com/datasets/tuyenldvn/caucafall
License(s): unknown
100% 7.74G/7.76G [01:34<00:00, 137MB/s]
100% 7.76G/7.76G [01:34<00:00, 88.4MB/s]


In [5]:
import zipfile
import os
import shutil

dataset_path = "/content/caucafall.zip"  # ZIP file
extract_path = "/content/Dataset_CAUCALFall"  # Temporary extraction folder
target_subjects = [f"Subject.{i}" for i in range(3, 11)]  # Subjects 3 to 10

# Unzip only the required subject folders
with zipfile.ZipFile(dataset_path, "r") as zip_ref:
    for file in zip_ref.namelist():
        if any(f"CAUCAFall/{sub}/" in file for sub in target_subjects):  # Check for subject paths
            zip_ref.extract(file, extract_path)

# Move extracted subject folders to Google Drive
drive_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"
os.makedirs(drive_path, exist_ok=True)  # Ensure the directory exists

for subject in target_subjects:
    src = os.path.join(extract_path, "Dataset CAUCAFall", "CAUCAFall", subject)
    dest = os.path.join(drive_path, subject)
    if os.path.exists(src):
        shutil.move(src, dest)
        print(f"Moved {subject} to Google Drive.")
    else:
        print(f"Warning: {subject} not found in extracted files!")

print("✅ Extraction and transfer complete!")


Moved Subject.3 to Google Drive.
Moved Subject.4 to Google Drive.
Moved Subject.5 to Google Drive.
Moved Subject.6 to Google Drive.
Moved Subject.7 to Google Drive.
Moved Subject.8 to Google Drive.
Moved Subject.9 to Google Drive.
Moved Subject.10 to Google Drive.
✅ Extraction and transfer complete!


In [6]:
!ls "/content/drive/My Drive/fall_detection_data/CAUCAFall"

resized_annotations  Subject.1	 Subject.2  Subject.4  Subject.6  Subject.8
resized_images	     Subject.10  Subject.3  Subject.5  Subject.7  Subject.9


In [7]:
!ls "/content/drive/My Drive/fall_detection_data/CAUCAFall/Subject.1"

'Fall backwards'  'Fall left'	'Fall sitting'	 Kneel		  'Sit down'
'Fall forward'	  'Fall right'	 Hop		'Pick up object'   Walk


In [13]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f"✅ Resized image saved to: {resized_image_path}")
    print(f"✅ Updated annotations saved to: {resized_annotation_path}")

# Process images for Subject.3
subject_folder = os.path.join(dataset_path, "Subject.3")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)


✅ Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.3/Fall sitting/css300007.png
✅ Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.3/Fall sitting/css300007.txt
✅ Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.3/Fall sitting/css300005.png
✅ Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.3/Fall sitting/css300005.txt
✅ Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.3/Fall sitting/css300136.png
✅ Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.3/Fall sitting/css300136.txt
✅ Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.3/Fall sitting/css300051.png
✅ Updated annotations saved to: /content/dr

In [17]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f" Resized image saved to: {resized_image_path}")
    print(f" Updated annotations saved to: {resized_annotation_path}")

subject_folder = os.path.join(dataset_path, "Subject.4")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)


 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.4/Fall sitting/css400164.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.4/Fall sitting/css400164.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.4/Fall sitting/css400194.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.4/Fall sitting/css400194.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.4/Fall sitting/css400008.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.4/Fall sitting/css400008.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.4/Fall sitting/css400077.png
 Updated annotations saved to: /content/drive/My D

In [18]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f" Resized image saved to: {resized_image_path}")
    print(f" Updated annotations saved to: {resized_annotation_path}")

subject_folder = os.path.join(dataset_path, "Subject.5")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)



 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.5/Fall sitting/css500013.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.5/Fall sitting/css500013.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.5/Fall sitting/css500019.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.5/Fall sitting/css500019.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.5/Fall sitting/css500036.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.5/Fall sitting/css500036.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.5/Fall sitting/css500189.png
 Updated annotations saved to: /content/drive/My D

In [19]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f" Resized image saved to: {resized_image_path}")
    print(f" Updated annotations saved to: {resized_annotation_path}")

subject_folder = os.path.join(dataset_path, "Subject.6")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)



 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.6/Fall sitting/css600172.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.6/Fall sitting/css600172.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.6/Fall sitting/css600117.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.6/Fall sitting/css600117.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.6/Fall sitting/css600087.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.6/Fall sitting/css600087.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.6/Fall sitting/css600184.png
 Updated annotations saved to: /content/drive/My D

In [6]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f" Resized image saved to: {resized_image_path}")
    print(f" Updated annotations saved to: {resized_annotation_path}")

subject_folder = os.path.join(dataset_path, "Subject.7")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)



 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.7/Fall backwards/cas700097.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.7/Fall backwards/cas700097.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.7/Fall backwards/cas700150.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.7/Fall backwards/cas700150.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.7/Fall backwards/cas700110.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.7/Fall backwards/cas700110.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.7/Fall backwards/cas700145.png
 Updated annotations saved to: /cont

In [7]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f" Resized image saved to: {resized_image_path}")
    print(f" Updated annotations saved to: {resized_annotation_path}")

subject_folder = os.path.join(dataset_path, "Subject.8")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)



 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.8/Fall backwards/cas800162.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.8/Fall backwards/cas800162.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.8/Fall backwards/cas800019.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.8/Fall backwards/cas800019.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.8/Fall backwards/cas800002.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.8/Fall backwards/cas800002.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.8/Fall backwards/cas800011.png
 Updated annotations saved to: /cont

In [8]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f" Resized image saved to: {resized_image_path}")
    print(f" Updated annotations saved to: {resized_annotation_path}")

subject_folder = os.path.join(dataset_path, "Subject.9")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)



 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.9/Fall backwards/cas900018.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.9/Fall backwards/cas900018.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.9/Fall backwards/cas900016.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.9/Fall backwards/cas900016.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.9/Fall backwards/cas900027.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.9/Fall backwards/cas900027.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.9/Fall backwards/cas900003.png
 Updated annotations saved to: /cont

In [9]:
import os
from PIL import Image

# Path to your dataset
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"

# Target size for resizing images
target_size = (320, 320)

# Base paths for resized images and annotations
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Function to resize image and adjust annotations
def resize_image_and_annotations(image_path, annotation_path, target_size):
    # Load the image
    image = Image.open(image_path)
    original_width, original_height = image.size

    # Resize the image
    image_resized = image.resize(target_size)

    # Read annotations
    if not os.path.exists(annotation_path):
        print(f"❌ Annotation missing for {image_path}")
        return  # Skip if annotation is missing

    with open(annotation_path, 'r') as f:
        annotations = f.readlines()

    # Adjust annotation coordinates based on the resize ratio
    new_annotations = []
    for annotation in annotations:
        parts = annotation.split()
        class_id, x1, y1, x2, y2 = map(float, parts)

        width_ratio = target_size[0] / original_width
        height_ratio = target_size[1] / original_height

        x1_resized = x1 * width_ratio
        y1_resized = y1 * height_ratio
        x2_resized = x2 * width_ratio
        y2_resized = y2 * height_ratio

        new_annotations.append(f"{class_id} {x1_resized} {y1_resized} {x2_resized} {y2_resized}\n")

    # Construct paths for resized files
    relative_path = os.path.relpath(image_path, dataset_path)
    resized_image_path = os.path.join(resized_images_base, relative_path)
    resized_annotation_path = os.path.join(resized_annotations_base, relative_path.replace(".png", ".txt"))

    # Ensure directories exist
    os.makedirs(os.path.dirname(resized_image_path), exist_ok=True)
    os.makedirs(os.path.dirname(resized_annotation_path), exist_ok=True)

    # Save the resized image and annotation
    image_resized.save(resized_image_path)
    with open(resized_annotation_path, 'w') as f:
        f.writelines(new_annotations)

    print(f" Resized image saved to: {resized_image_path}")
    print(f" Updated annotations saved to: {resized_annotation_path}")

subject_folder = os.path.join(dataset_path, "Subject.10")

for activity in os.listdir(subject_folder):
    activity_folder = os.path.join(subject_folder, activity)
    if os.path.isdir(activity_folder):
        for filename in os.listdir(activity_folder):
            if filename.endswith(".png"):  # Assuming images are in PNG format
                image_path = os.path.join(activity_folder, filename)
                annotation_path = image_path.replace(".png", ".txt")
                resize_image_and_annotations(image_path, annotation_path, target_size)



 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.10/Fall backwards/cas1000035.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.10/Fall backwards/cas1000035.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.10/Fall backwards/cas1000027.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.10/Fall backwards/cas1000027.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.10/Fall backwards/cas1000007.png
 Updated annotations saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_annotations/Subject.10/Fall backwards/cas1000007.txt
 Resized image saved to: /content/drive/My Drive/fall_detection_data/CAUCAFall/resized_images/Subject.10/Fall backwards/cas1000016.png
 Updated annotations s

In [10]:
import os
import shutil
import random
from PIL import Image

# Set dataset paths
dataset_path = "/content/drive/My Drive/fall_detection_data/CAUCAFall"
resized_images_base = os.path.join(dataset_path, "resized_images")
resized_annotations_base = os.path.join(dataset_path, "resized_annotations")

# Define split ratios
train_ratio = 0.7
val_ratio = 0.2
test_ratio = 0.1

# Output directories
split_base = os.path.join(dataset_path, "split_data")
train_img_dir = os.path.join(split_base, "train", "images")
train_label_dir = os.path.join(split_base, "train", "labels")
val_img_dir = os.path.join(split_base, "val", "images")
val_label_dir = os.path.join(split_base, "val", "labels")
test_img_dir = os.path.join(split_base, "test", "images")
test_label_dir = os.path.join(split_base, "test", "labels")

# Create folders if they don’t exist
for folder in [train_img_dir, train_label_dir, val_img_dir, val_label_dir, test_img_dir, test_label_dir]:
    os.makedirs(folder, exist_ok=True)

# Collect all image paths recursively
all_images = []
for subject in os.listdir(resized_images_base):
    subject_path = os.path.join(resized_images_base, subject)
    if os.path.isdir(subject_path):
        for activity in os.listdir(subject_path):
            activity_folder = os.path.join(subject_path, activity)
            if os.path.isdir(activity_folder):
                for filename in os.listdir(activity_folder):
                    if filename.endswith(".png"):  # Assuming images are PNG format
                        img_path = os.path.join(activity_folder, filename)
                        annotation_path = img_path.replace(resized_images_base, resized_annotations_base).replace(".png", ".txt")
                        if os.path.exists(annotation_path):  # Ensure annotation file exists
                            all_images.append((img_path, annotation_path))

# Shuffle dataset
random.shuffle(all_images)

# Split dataset
total_count = len(all_images)
train_split = int(total_count * train_ratio)
val_split = int(total_count * (train_ratio + val_ratio))

train_set = all_images[:train_split]
val_set = all_images[train_split:val_split]
test_set = all_images[val_split:]

# Function to move files
def move_files(data, img_dest, label_dest):
    for img_path, label_path in data:
        shutil.copy(img_path, os.path.join(img_dest, os.path.basename(img_path)))
        shutil.copy(label_path, os.path.join(label_dest, os.path.basename(label_path)))

# Move files into respective folders
move_files(train_set, train_img_dir, train_label_dir)
move_files(val_set, val_img_dir, val_label_dir)
move_files(test_set, test_img_dir, test_label_dir)

# Final message
print("\n Train (70%), Validation (20%), and Test (10%) split complete!")



 Train (70%), Validation (20%), and Test (10%) split complete! 
